In [1]:
from model import *
from similarity import *
import csv

In [2]:
def create_similarity_matrix(filename, key):
    with open(filename) as file:
        similarity_matrix = {}

        for line in csv.DictReader(file, skipinitialspace=True):
            for k, v in line.items():
                if k == key:
                    key_v = v
                    similarity_matrix[key_v] = {}
                else:
                    similarity_matrix[key_v][k] = float(v)

        return similarity_matrix

In [3]:
case_base = CaseBase.from_csv(
    "data/SIM_001.csv",
    problem_fields = ("v", "v_left", "v_front", "d_left", "d_front", "type_left", "type_front", "radius_curve(m)", "slope_street", "street_type", "time", "weather", "type_vehicle", "speed_limit(km/h)"),
    solution_fields = ("action"),
    encoding = "utf-8",
    delimiter = ";",
    set_int = True
)
print(case_base)
case_base[:3]

CaseBase(cases=499, fields=[('v', 'v_left', 'v_front', 'd_left', 'd_front', 'type_left', 'type_front', 'radius_curve(m)', 'slope_street', 'street_type', 'time', 'weather', 'type_vehicle', 'speed_limit(km/h)'), 'action'])


[Case(problem={'v_left': 36.5, 'v_front': 23.0, 'd_left': -56.0, 'd_front': 45.0, 'type_left': 'sportscar', 'type_front': 'truck', 'radius_curve(m)': 2237.0, 'slope_street': 'flat', 'street_type': 'country_road (separated)', 'time': 'night', 'weather': 'dry', 'type_vehicle': 'car', 'speed_limit(km/h)': 100.0}, solution={'action': 'continue'}),
 Case(problem={'v_left': 32.0, 'v_front': 28.0, 'd_left': -114.0, 'd_front': 44.0, 'type_left': 'motorcycle', 'type_front': 'car', 'radius_curve(m)': 3891.0, 'slope_street': 'ascending', 'street_type': 'autobahn', 'time': 'night', 'weather': 'dry', 'type_vehicle': 'truck', 'speed_limit(km/h)': 250.0}, solution={'action': 'continue'}),
 Case(problem={'v_left': 43.0, 'v_front': 31.5, 'd_left': -98.0, 'd_front': 60.0, 'type_left': 'truck', 'type_front': 'car', 'radius_curve(m)': 1720.0, 'slope_street': 'flat', 'street_type': 'autobahn', 'time': 'dusk', 'weather': 'rain', 'type_vehicle': 'car', 'speed_limit(km/h)': 130.0}, solution={'action': 'contin

In [4]:
case_base.add_symbolic_sim(
    field = "type_left",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base.add_symbolic_sim(
    field = "type_front",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base.add_symbolic_sim(
    field = "type_vehicle",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base.add_symbolic_sim(
    field = "slope_street",
    similarity_matrix = create_similarity_matrix("data/street_slope_sim.csv", "type_street_slope")
)

case_base.add_symbolic_sim(
    field = "time",
    similarity_matrix = create_similarity_matrix("data/time_type_sim.csv", "type_time")
)

case_base.add_symbolic_sim(
    field = "weather",
    similarity_matrix = create_similarity_matrix("data/weather_type_sim.csv", "type_weather")
)


In [5]:
query = Query.from_problems(
    v = 28,
    v_left = 37,
    v_front = 22.5,
    d_left = -20,
    d_front = 51,
    radius_curve = 2000,
    speed_limit = 200,
    type_vehicle = "motorcycle",
    type_left = "motorcycle",
    type_front = "motorcycle",
)

# sim_funcs: manhattan_sim, euclid_sim
retrieved = case_base.retrieve(
    query,
    v_left = euclid_sim,
    v_front = euclid_sim,
    d_left = euclid_sim,
    d_front = euclid_sim,
    radius_curve = manhattan_sim,
    speed_limit = manhattan_sim,
    type_vehicle = symbolic_sim,
    type_left = symbolic_sim,
    type_front = symbolic_sim,
)

print("Your Query:")
for k, v in query.problem.items():
    print(f"  - {k} = {v}")
print()
print("I recommend you this car:")
print(" ".join(retrieved.solution.values()).capitalize())
print()
print("Explanation:")
for field, sim_val in retrieved.sim_per_field.items():
    print(f"  - {field} =", retrieved.problem[field], f"(similarity: {sim_val:.2f})")

Your Query:
  - v = 28
  - v_left = 37
  - v_front = 22.5
  - d_left = -20
  - d_front = 51
  - radius_curve = 2000
  - speed_limit = 200
  - type_vehicle = motorcycle
  - type_left = motorcycle
  - type_front = motorcycle

I recommend you this car:
Accelerated_lane_change

Explanation:
  - v_left = 37.0 (similarity: 1.00)
  - v_front = 22.5 (similarity: 1.00)
  - d_left = -17.0 (similarity: 0.25)
  - d_front = 51.0 (similarity: 1.00)
  - radius_curve(m) = 3020.0 (similarity: 0.00)
  - speed_limit(km/h) = 120.0 (similarity: 0.01)
  - type_vehicle = car (similarity: 0.50)
  - type_left = truck (similarity: 0.50)
  - type_front = truck (similarity: 0.50)
